In [1]:
import requests 
import json 
import pandas as pd 
import numpy as np  
#import mysql.connector
import datetime as dt  
from operator import truediv
import matplotlib.pyplot as plt 
 
from sklearn.preprocessing import MinMaxScaler

from tqdm import tqdm_notebook as tqdm

from darts import TimeSeries, concatenate
from darts.dataprocessing.transformers import Scaler
from darts.models import TFTModel
from darts.metrics import mape
from darts.utils.statistics import check_seasonality, plot_acf
from darts.utils.timeseries_generation import datetime_attribute_timeseries
from darts.utils.likelihood_models import QuantileRegression



In [2]:
plt.style.use('ggplot')
plt.rcParams['font.family'] = 'sans-serif' 
plt.rcParams['font.serif'] = 'Ubuntu' 
plt.rcParams['font.monospace'] = 'Ubuntu Mono' 
plt.rcParams['font.size'] = 14 
plt.rcParams['axes.labelsize'] = 12 
plt.rcParams['axes.labelweight'] = 'bold' 
plt.rcParams['axes.titlesize'] = 12 
plt.rcParams['xtick.labelsize'] = 12 
plt.rcParams['ytick.labelsize'] = 12 
plt.rcParams['legend.fontsize'] = 12 
plt.rcParams['figure.titlesize'] = 12 
plt.rcParams['image.cmap'] = 'jet' 
plt.rcParams['image.interpolation'] = 'none' 
plt.rcParams['figure.figsize'] = (12, 10) 
plt.rcParams['axes.grid']=True
plt.rcParams['lines.linewidth'] = 2 
plt.rcParams['lines.markersize'] = 8
colors = ['xkcd:pale orange', 'xkcd:sea blue', 'xkcd:pale red', 'xkcd:sage green', 'xkcd:terra cotta', 'xkcd:dull purple', 'xkcd:teal', 'xkcd: goldenrod', 'xkcd:cadet blue',
'xkcd:scarlet']

In [128]:
import csv
with open('exdata.csv', newline='') as f:
    reader = csv.reader(f)
    myresult0 = list(reader)


myresult0=np.array(myresult0)
df=pd.DataFrame(data=myresult0[1:,1:-3],             index=myresult0[1:,1],          columns=myresult0[0,1:-3])
df["open_time"]=pd.to_datetime(df.open_time.astype(float)/1000, unit='s')

df.index=df['open_time']

df=df.sort_index(ascending=True,axis=0)
df["o"]=df.o.astype(float)
df["h"]=df.h.astype(float)
df["c"]=df.c.astype(float)
df["l"]=df.l.astype(float)
df["v"]=df.v.astype(float)
df["qav"]=df.qav.astype(float)
df["num_trades"]=df.num_trades.astype(float)
df["taker_base_vol"]=df.taker_base_vol.astype(float)
df["taker_quote_vol"]=df.taker_quote_vol.astype(float)
df

open_time       o       h       l       c  \
open_time                                                                 
2021-12-27 03:46:00 2021-12-27 03:46:00  156.60  156.90  156.60  156.70   
2021-12-27 03:47:00 2021-12-27 03:47:00  156.80  156.90  156.70  156.90   
2021-12-27 03:48:00 2021-12-27 03:48:00  156.80  157.00  156.80  156.90   
2021-12-27 03:49:00 2021-12-27 03:49:00  156.90  156.90  156.80  156.90   
2021-12-27 03:50:00 2021-12-27 03:50:00  156.90  156.90  156.60  156.60   
...                                 ...     ...     ...     ...     ...   
2023-10-01 11:54:00 2023-10-01 11:54:00   67.47   67.47   67.41   67.42   
2023-10-01 11:55:00 2023-10-01 11:55:00   67.42   67.48   67.42   67.44   
2023-10-01 11:56:00 2023-10-01 11:56:00   67.44   67.47   67.44   67.46   
2023-10-01 11:57:00 2023-10-01 11:57:00   67.46   67.47   67.43   67.45   
2023-10-01 11:58:00 2023-10-01 11:58:00   67.45   67.45   67.41   67.42   

                            v     close_time           qav  num_trades  \
open_time                                                                
2021-12-27 03:46:00  2163.393  1640576819999  339211.35800       260.0   
2021-12-27 03:47:00   658.301  1640576879999  103265.82580       106.0   
2021-12-27 03:48:00   246.201  1640576939999   38628.26330       154.0   
2021-12-27 03:49:00   185.978  1640576999999   29178.89930        49.0   
2021-12-27 03:50:00    98.526  1640577059999   15442.86910        77.0   
...                       ...            ...           ...         ...   
2023-10-01 11:54:00   132.637  1696161299999    8942.58033        47.0   
2023-10-01 11:55:00   445.585  1696161359999   30061.18761        73.0   
2023-10-01 11:56:00   127.692  1696161419999    8613.77209        34.0   
2023-10-01 11:57:00   177.039  1696161479999   11941.19650        42.0   
2023-10-01 11:58:00   653.254  1696161539999   44044.57947        61.0   

                     taker_base_vol  taker_quote_vol  
open_time                                             
2021-12-27 03:46:00        2049.904     321422.29660  
2021-12-27 03:47:00         623.404      97794.28910  
2021-12-27 03:48:00         100.498      15768.32880  
2021-12-27 03:49:00          52.947       8307.38430  
2021-12-27 03:50:00           6.143        963.24320  
...                             ...              ...  
2023-10-01 11:54:00          44.501       3000.50936  
2023-10-01 11:55:00         273.277      18435.83875  
2023-10-01 11:56:00          86.903       5862.43945  
2023-10-01 11:57:00          92.575       6244.46175  
2023-10-01 11:58:00          39.503       2663.84783  

[916594 rows x 11 columns]

In [129]:
#df.index.day_of_week
df.index.month

Int64Index([12, 12, 12, 12, 12, 12, 12, 12, 12, 12,
            ...
            10, 10, 10, 10, 10, 10, 10, 10, 10, 10],
           dtype='int64', name='open_time', length=916594)

In [130]:
df_rs = df.resample('7T', label='right', closed='right').agg({'o':'first','h':'max','l':'min','c':'last','v':'sum','num_trades':'sum','qav':'sum','taker_base_vol':'sum','taker_quote_vol':'sum'})
df_rs

o       h       l       c         v  num_trades  \
open_time                                                                   
2021-12-27 03:51:00  156.60  157.00  156.60  156.70  3352.645       647.0   
2021-12-27 03:58:00  156.80  156.80  156.50  156.70   916.475       342.0   
2021-12-27 04:05:00  156.60  156.70  156.20  156.20  1571.132       444.0   
2021-12-27 04:12:00  156.30  156.40  156.10  156.30   555.308       224.0   
2021-12-27 04:19:00  156.40  156.50  156.10  156.20   686.940       276.0   
...                     ...     ...     ...     ...       ...         ...   
2023-10-01 11:31:00   67.31   67.41   67.31   67.41  2120.521       299.0   
2023-10-01 11:38:00   67.40   67.52   67.39   67.48  1858.447       362.0   
2023-10-01 11:45:00   67.48   67.62   67.48   67.59  2628.163       402.0   
2023-10-01 11:52:00   67.59   67.65   67.41   67.42  2440.443       461.0   
2023-10-01 11:59:00   67.42   67.48   67.41   67.42  2496.682       353.0   

                              qav  taker_base_vol  taker_quote_vol  
open_time                                                           
2021-12-27 03:51:00  525765.76370        2833.142     444294.09020  
2021-12-27 03:58:00  143510.62850         458.214      71764.94140  
2021-12-27 04:05:00  245787.10520         443.146      69363.34100  
2021-12-27 04:12:00   86760.19670         265.701      41522.20010  
2021-12-27 04:19:00  107419.23140         303.674      47499.31530  
...                           ...             ...              ...  
2023-10-01 11:31:00  142839.37563        1591.670     107218.69491  
2023-10-01 11:38:00  125395.53599        1231.197      83076.07031  
2023-10-01 11:45:00  177553.95315        1850.271     125002.17993  
2023-10-01 11:52:00  164781.56528         777.572      52516.48259  
2023-10-01 11:59:00  168387.68432         694.353      46836.45363  

[132345 rows x 9 columns]

In [131]:
df_rs=df_rs.fillna(method='ffill')

In [132]:
# Get the 26-day EMA of the closing price
k = df_rs['c'].ewm(span=12, adjust=False, min_periods=12).mean()
# Get the 12-day EMA of the closing price
d = df_rs['c'].ewm(span=26, adjust=False, min_periods=26).mean()
# Subtract the 26-day EMA from the 12-Day EMA to get the MACD
macd = k - d
# Get the 9-Day EMA of the MACD for the Trigger line
macd_s = macd.ewm(span=9, adjust=False, min_periods=9).mean()
# Calculate the difference between the MACD - Trigger for the Convergence/Divergence value
macd_h = macd - macd_s
# Add all of our new values for the MACD to the dataframe
df_rs['macd'] = df_rs.index.map(macd)
df_rs['macd_h'] = df_rs.index.map(macd_h)
df_rs['macd_s'] = df_rs.index.map(macd_s)

df_rs["price"]=np.array(df_rs["c"]).tolist()


df_rs2=df_rs[1:]
df_rs2["c"]=(((np.array(df_rs["c"][1:])/np.array(df_rs["c"][:-1]))-1)*100).tolist()
df=df_rs2[1:]
df["num_trades"]=(df["num_trades"]/2000)
df.loc[df["num_trades"]>1.0,"num_trades"]=1
print(int(max(df["v"])/12))
df["v"]=df["v"]/(int(max(df["v"])/12))
df.loc[df["v"]>1,"v"]=1
df["taker_base_vol"]=(df["taker_base_vol"]/10000)
df.loc[df["taker_base_vol"]>1.0,"taker_base_vol"]=1
df["h"]=df["h"]/df["price"]
df["l"]=df["l"]/df["price"]
###df2 = np.asarray(df.drop(columns=['o','price','taker_quote_vol',"qav"]))
df2x = df.drop(columns=['c','o','price','taker_quote_vol',"qav"])
df2y = df["c"]
df2x

19465


C:\Users\DABC\AppData\Local\Temp\ipykernel_17940\3865196209.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_rs2["c"]=(((np.array(df_rs["c"][1:])/np.array(df_rs["c"][:-1]))-1)*100).tolist()
C:\Users\DABC\AppData\Local\Temp\ipykernel_17940\3865196209.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["num_trades"]=(df["num_trades"]/2000)
C:\Users\DABC\AppData\Local\Temp\ipykernel_17940\3865196209.py:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Tr

h         l         v  num_trades  taker_base_vol  \
open_time                                                                       
2021-12-27 04:05:00  1.003201  1.000000  0.080716      0.2220        0.044315   
2021-12-27 04:12:00  1.000640  0.998720  0.028529      0.1120        0.026570   
2021-12-27 04:19:00  1.001921  0.999360  0.035291      0.1380        0.030367   
2021-12-27 04:26:00  1.001282  0.999359  0.049653      0.1660        0.047911   
2021-12-27 04:33:00  1.000000  0.998720  0.037816      0.1445        0.031561   
...                       ...       ...       ...         ...             ...   
2023-10-01 11:31:00  1.000000  0.998517  0.108940      0.1495        0.159167   
2023-10-01 11:38:00  1.000593  0.998666  0.095476      0.1810        0.123120   
2023-10-01 11:45:00  1.000444  0.998373  0.135020      0.2010        0.185027   
2023-10-01 11:52:00  1.003411  0.999852  0.125376      0.2305        0.077757   
2023-10-01 11:59:00  1.000890  0.999852  0.128265      0.1765        0.069435   

                         macd    macd_h    macd_s  
open_time                                          
2021-12-27 04:05:00       NaN       NaN       NaN  
2021-12-27 04:12:00       NaN       NaN       NaN  
2021-12-27 04:19:00       NaN       NaN       NaN  
2021-12-27 04:26:00       NaN       NaN       NaN  
2021-12-27 04:33:00       NaN       NaN       NaN  
...                       ...       ...       ...  
2023-10-01 11:31:00  0.261514 -0.000513  0.262026  
2023-10-01 11:38:00  0.266595  0.003655  0.262940  
2023-10-01 11:45:00  0.276312  0.010698  0.265614  
2023-10-01 11:52:00  0.267216  0.001281  0.265935  
2023-10-01 11:59:00  0.257044 -0.007113  0.264157  

[132343 rows x 8 columns]

In [133]:
df2y=pd.DataFrame(df2y)
df2y=df2y[37:]
df2x=df2x[36:-1]
df2x.index = df2y.index
df2ytr=df2y[:-10000]

In [18]:
df2y

c
open_time                    
2021-12-27 08:24:00 -0.063980
2021-12-27 08:31:00  0.064020
2021-12-27 08:38:00  0.063980
2021-12-27 08:45:00 -0.127877
2021-12-27 08:52:00 -0.128041
...                       ...
2023-10-01 11:31:00  0.148566
2023-10-01 11:38:00  0.103842
2023-10-01 11:45:00  0.163011
2023-10-01 11:52:00 -0.251516
2023-10-01 11:59:00  0.000000

[132306 rows x 1 columns]

In [20]:

train_transformed = TimeSeries.from_dataframe(df2ytr)
y_transformed = TimeSeries.from_dataframe(df2y)
covariates = TimeSeries.from_dataframe(df2x)

covariates = covariates.stack(datetime_attribute_timeseries(covariates, attribute="dayofweek", one_hot=False))
covariates = covariates.stack(
    datetime_attribute_timeseries(covariates, attribute="hour", one_hot=False)
)
covariates = covariates.stack(
    TimeSeries.from_times_and_values(
        times=covariates.time_index,
        values=np.arange(len(covariates)),
        columns=["linear_increase"],
    )
)
covariates = covariates.astype(np.float32)
covariates_transformed=covariates


tftmodel=TFTModel(input_chunk_length=19,output_chunk_length=1,hidden_size=70,lstm_layers=7,num_attention_heads=7,dropout=0.2,n_epochs=20, force_reset=True,
)

tftmodel.fit(train_transformed ,future_covariates=covariates_transformed, verbose=True)
tftmodel.save("full-ltc-tftmodel.pt")



GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs

   | Name                              | Type                             | Params
----------------------------------------------------------------------------------------
0  | train_metrics                     | MetricCollection                 | 0     
1  | val_metrics                       | MetricCollection                 | 0     
2  | input_embeddings                  | _MultiEmbedding                  | 0     
3  | static_covariates_vsn             | _VariableSelectionNetwork        | 0     
4  | encoder_vsn                       | _VariableSelectionNetwork        | 23.8 K
5  | decoder_vsn                       | _VariableSelectionNetwork        | 21.7 K
6  | static_context_grn                | _GatedResidualNetwork            | 20.0 K
7  | static_context_hidden_encoder_grn | _GatedResidualNetwork            | 20.0 K
8  | static_cont

Training: |          | 0/? [00:00<?, ?it/s]

`Trainer.fit` stopped: `max_epochs=20` reached.


In [4]:
tftmodel=TFTModel.load("full-ltc-tftmodel.pt")

In [5]:
def eval_model(model, n, actual_series, val_series):
    num_samples=7
    pred_series = model.predict(n=n, num_samples=num_samples)
    lowest_q ,low_q , high_q ,highest_q= 0.01 ,0.25 , 0.75 , 0.99
    label_q_outer=f"{int(lowest_q*100)}-{int(highest_q*100)}th percentiles"
    label_q_inner=f"{int(low_q*100)}-{int(high_q*100)}th percentiles"
    # plot actual series
    plt.figure(figsize=(10,6))
    actual_series[pred_series.start_time(): pred_series.end_time()].plot(label="actual")

    # plot prediction with quantile ranges
    pred_series.plot(low_quantile=lowest_q, high_quantile=highest_q, label=label_q_outer)
    pred_series.plot(low_quantile=low_q, high_quantile=high_q, label=label_q_inner)

    plt.title("MAPE: {:.2f}%".format(mape(val_series+1, pred_series+1)))
    plt.legend()


eval_model(tftmodel, 10, y_transformed, y_transformed[len(train_transformed)+1:])

NameError: name 'y_transformed' is not defined

In [25]:
y_transformed

<TimeSeries (DataArray) (open_time: 132306, component: 1, sample: 1)>
array([[[-0.06397953]],

       [[ 0.06402049]],

       [[ 0.06397953]],

       ...,

       [[ 0.16301126]],

       [[-0.2515165 ]],

       [[ 0.        ]]])
Coordinates:
  * open_time  (open_time) datetime64[ns] 2021-12-27T08:24:00 ... 2023-10-01T...
  * component  (component) object 'c'
Dimensions without coordinates: sample
Attributes:
    static_covariates:  None
    hierarchy:          None

In [26]:
y_transformed[len(train_transformed):]

<TimeSeries (DataArray) (open_time: 10000, component: 1, sample: 1)>
array([[[-0.0240616 ]],

       [[-0.08423586]],

       [[-0.14452607]],

       ...,

       [[ 0.16301126]],

       [[-0.2515165 ]],

       [[ 0.        ]]])
Coordinates:
  * open_time  (open_time) datetime64[ns] 2023-08-13T21:26:00 ... 2023-10-01T...
  * component  (component) object 'c'
Dimensions without coordinates: sample
Attributes:
    static_covariates:  None
    hierarchy:          None

In [13]:
####### for test -- with deep selector --part 1: test deep selector

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dropout
from tensorflow.keras.layers import Bidirectional
from tensorflow.keras.layers import Embedding
from tensorflow.keras.preprocessing import sequence
from tensorflow.keras.models import load_model
df = pd.read_csv("exdata-2w-test.csv")

df["open_time"]=pd.to_datetime(df.open_time/1000, unit='s')
df.index=df['open_time']
df=df.sort_index(ascending=True,axis=0)
df_rs = df.resample('7T', label='right', closed='right').agg({'o':'first','h':'max','l':'min','c':'last','v':'sum','num_trades':'sum','qav':'sum','taker_base_vol':'sum','taker_quote_vol':'sum'})
df_rs=df_rs.fillna(method='ffill')
# Get the 26-day EMA of the closing price
k = df_rs['c'].ewm(span=12, adjust=False, min_periods=12).mean()
# Get the 12-day EMA of the closing price
d = df_rs['c'].ewm(span=26, adjust=False, min_periods=26).mean()
# Subtract the 26-day EMA from the 12-Day EMA to get the MACD
macd = k - d
# Get the 9-Day EMA of the MACD for the Trigger line
macd_s = macd.ewm(span=9, adjust=False, min_periods=9).mean()
# Calculate the difference between the MACD - Trigger for the Convergence/Divergence value
macd_h = macd - macd_s
# Add all of our new values for the MACD to the dataframe
df_rs['macd'] = df_rs.index.map(macd)
df_rs['macd_h'] = df_rs.index.map(macd_h)
df_rs['macd_s'] = df_rs.index.map(macd_s)

df_rs["price"]=np.array(df_rs["c"]).tolist()


df_rs2=df_rs[1:]
df_rs2["c"]=(((np.array(df_rs["c"][1:])/np.array(df_rs["c"][:-1]))-1)*100).tolist()
df=df_rs2[1:]
df["num_trades"]=(df["num_trades"]/2000)
df.loc[df["num_trades"]>1.0,"num_trades"]=1
print(int(max(df["v"])/12))
df["v"]=df["v"]/(int(max(df["v"])/12))
df.loc[df["v"]>1,"v"]=1
df["taker_base_vol"]=(df["taker_base_vol"]/10000)
df.loc[df["taker_base_vol"]>1.0,"taker_base_vol"]=1
df["h"]=df["h"]/df["price"]
df["l"]=df["l"]/df["price"]
###df2 = np.asarray(df.drop(columns=['o','price','taker_quote_vol',"qav"]))
df2x = df.drop(columns=['c','o','price','taker_quote_vol',"qav"])
df2y = df["c"]
df2y=pd.DataFrame(df2y)
'''
df=df[36:]
df2y=df2y[37:]
df2x=df2x[36:-1]
df2x.index = df2y.index
'''
df=df[37:]
df2y=df2y[37:]
df2x=df2x[37:]

5968


C:\Users\DABC\AppData\Local\Temp\ipykernel_10168\1364115936.py:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_rs2["c"]=(((np.array(df_rs["c"][1:])/np.array(df_rs["c"][:-1]))-1)*100).tolist()
C:\Users\DABC\AppData\Local\Temp\ipykernel_10168\1364115936.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["num_trades"]=(df["num_trades"]/2000)
C:\Users\DABC\AppData\Local\Temp\ipykernel_10168\1364115936.py:42: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Tr

In [7]:
def model_test(actual_series,pcov):
    num_samples=7
    pcov = pcov.astype(np.float32)
    pred_series = tftmodel.predict(n=1,series=actual_series ,future_covariates=pcov, num_samples=num_samples,n_jobs=-1)
    return pred_series[0].quantile(0.5).values()[0]

In [53]:
pd.DataFrame(df2x[10:20])

h         l         v  num_trades  taker_base_vol  \
open_time                                                                       
2023-08-23 02:15:00  1.001692  0.999692  0.434072      0.1705        0.124003   
2023-08-23 02:22:00  1.000000  0.998616  0.262723      0.1125        0.109105   
2023-08-23 02:29:00  1.000154  0.998464  0.099302      0.0935        0.039494   
2023-08-23 02:36:00  1.000614  0.999232  0.110839      0.0935        0.023362   
2023-08-23 02:43:00  1.000000  0.999079  0.159622      0.0705        0.017371   
2023-08-23 02:50:00  1.002458  0.999539  0.333873      0.1635        0.049902   
2023-08-23 02:57:00  1.002155  1.000000  0.142931      0.0875        0.019256   
2023-08-23 03:04:00  1.000770  0.999538  0.142341      0.0900        0.038181   
2023-08-23 03:11:00  1.000615  0.998308  0.114385      0.0910        0.051408   
2023-08-23 03:18:00  1.002620  0.999846  0.102591      0.0920        0.020186   

                         macd    macd_h    macd_s  
open_time                                          
2023-08-23 02:15:00  0.136167 -0.003788  0.139955  
2023-08-23 02:22:00  0.136278 -0.002941  0.139219  
2023-08-23 02:29:00  0.142789  0.002856  0.139933  
2023-08-23 02:36:00  0.147061  0.005702  0.141359  
2023-08-23 02:43:00  0.150328  0.007175  0.143153  
2023-08-23 02:50:00  0.147185  0.003226  0.143959  
2023-08-23 02:57:00  0.133473 -0.008389  0.141862  
2023-08-23 03:04:00  0.117220 -0.019713  0.136934  
2023-08-23 03:11:00  0.111128 -0.020645  0.131772  
2023-08-23 03:18:00  0.094718 -0.029644  0.124361

In [14]:
####### test 2w
tp , tn ,fp,fn,allcorrect,allpred,sellsig,buysig=0,0,0,0,0,0,0,0
TestUSDTAmount=100
TestLTCAmount=0
for cc in range(1,len(df)-21):
    FLAGincprice  , FLAGincmoreprice, FLAGdecmoreprice, FLAGmarkovinc,FLAGincspeed,vote,risk=0,0,0,0,0,0,0
    oldy=np.array(df2y["c"][cc:cc+19].tolist())
    y=np.array(df2y["c"][cc+19].tolist())
    
    oldy=pd.DataFrame(oldy,columns=['c'])
    oldy.index=pd.to_datetime(df2x[cc:cc+19].index,errors='ignore')
    #print (oldy)
    #print (df2x[cc:cc+19])
    #break
    #cov=pd.DataFrame(df2x[cc:cc+20])
    #cov.index=oldy.index
    test_transformed = TimeSeries.from_dataframe(oldy)
    #print (test_transformed)
    #break
    pastcov=TimeSeries.from_dataframe(pd.DataFrame(df2x[cc:cc+20]))
    #pastcov=TimeSeries.from_dataframe(cov)
    pastcov = pastcov.stack(datetime_attribute_timeseries(pastcov, attribute="dayofweek", one_hot=False ))
    pastcov = pastcov.stack(datetime_attribute_timeseries(pastcov, attribute="hour", one_hot=False) )
    pastcov = pastcov.stack(
        TimeSeries.from_times_and_values(
            times=pastcov.time_index,
            values=np.arange(len(pastcov)),
            columns=["linear_increase"],
        )
    )
    price=model_test(test_transformed,pastcov)
    price=price[0]
    # BUY Signal  and FLAGincmoreprice
    if(price>=0):
        buysig=buysig+1
        if(y>=0):
            tp=tp+1
        else:
            fp=fp+1
        
        TestLTCAmount=TestLTCAmount+float(TestUSDTAmount/float(np.array(df["price"][cc+18])))
        TestUSDTAmount=0
    
    else :
        sellsig=sellsig+1
        if(y<=0):
            tn=tn+1
        else:
            fn=fn+1
        TestUSDTAmount=TestUSDTAmount+float(TestLTCAmount*float(np.array(df["price"][cc+18])))
        TestLTCAmount=0

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
C:\Users\DABC\AppData\Roaming\jupyterlab-desktop\jlab_server\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:441: The 'predict_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=7` in the `DataLoader` to improve performance.


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
C:\Users\DABC\AppData\Roaming\jupyterlab-desktop\jlab_server\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:441: The 'predict_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=7` in the `DataLoader` to improve performance.


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
C:\Users\DABC\AppData\Roaming\jupyterlab-desktop\jlab_server\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:441: The 'predict_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=7` in the `DataLoader` to improve performance.


...

Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
C:\Users\DABC\AppData\Roaming\jupyterlab-desktop\jlab_server\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:441: The 'predict_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=7` in the `DataLoader` to improve performance.


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
C:\Users\DABC\AppData\Roaming\jupyterlab-desktop\jlab_server\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:441: The 'predict_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=7` in the `DataLoader` to improve performance.


Predicting: |          | 0/? [00:00<?, ?it/s]

In [15]:
#print("ee"+ str(TestLTCAmount*float(myresult0[-1]))
#TestUSDTAmount
TestLTCAmount*float(np.array(df["price"][len(df)-1]))

95.94779700003882

In [125]:
#print("ee"+ str(TestLTCAmount*float(myresult0[-1]))
TestUSDTAmount
#TestLTCAmount*float(np.array(df["price"][len(df)-1]))

104.19140435876069

In [126]:
print("tp:"+str(tp)+" tn:"+str(tn)+" fp:"+str(fp)+" fn:"+str(fn))

tp:805 tn:634 fp:786 fn:595


In [140]:
df

o         h         l         c         v  \
open_time                                                            
2023-08-23 01:05:00  64.78  1.002319  1.000000 -0.108091  0.207315   
2023-08-23 01:12:00  64.69  1.000309  0.998919  0.092750  0.109815   
2023-08-23 01:19:00  64.75  1.000771  0.998611  0.092664  0.219654   
2023-08-23 01:26:00  64.81  1.002319  0.999691 -0.216016  0.167335   
2023-08-23 01:33:00  64.68  1.000618  0.999072  0.015463  0.219763   
...                    ...       ...       ...       ...       ...   
2023-09-05 20:04:00  63.06  1.000793  0.999683 -0.047574  0.105073   
2023-09-05 20:11:00  63.04  1.000634  0.999683  0.031731  0.110810   
2023-09-05 20:18:00  63.06  1.001268  0.999841  0.031721  0.083201   
2023-09-05 20:25:00  63.07  1.000476  0.999683  0.015855  0.057320   
2023-09-05 20:32:00  63.07  1.000317  0.999208  0.047559  0.045857   

                     num_trades          qav  taker_base_vol  taker_quote_vol  \
open_time                                                                       
2023-08-23 01:05:00      0.1355  80141.96408        0.054848      35529.57040   
2023-08-23 01:12:00      0.0975  42420.03428        0.031956      20686.10874   
2023-08-23 01:19:00      0.1125  84964.78687        0.088173      57156.09035   
2023-08-23 01:26:00      0.0915  64609.81340        0.028230      18265.05785   
2023-08-23 01:33:00      0.1005  84848.25773        0.110272      71342.20970   
...                         ...          ...             ...              ...   
2023-09-05 20:04:00      0.0825  39527.21648        0.018750      11819.74811   
2023-09-05 20:11:00      0.1000  41698.81910        0.030114      18987.71704   
2023-09-05 20:18:00      0.1050  31335.54841        0.019324      12196.32210   
2023-09-05 20:25:00      0.0690  21582.17306        0.010873       6859.50568   
2023-09-05 20:32:00      0.0420  17265.66719        0.005112       3224.77933   

                         macd    macd_h    macd_s  price  
open_time                                                 
2023-08-23 01:05:00  0.173237 -0.027436  0.200673  64.69  
2023-08-23 01:12:00  0.158116 -0.034046  0.192162  64.75  
2023-08-23 01:19:00  0.149253 -0.034327  0.183580  64.81  
2023-08-23 01:26:00  0.129440 -0.043312  0.172752  64.67  
2023-08-23 01:33:00  0.113240 -0.047610  0.160850  64.68  
...                       ...       ...       ...    ...  
2023-09-05 20:04:00  0.008374 -0.025421  0.033795  63.03  
2023-09-05 20:11:00 -0.000813 -0.027686  0.026873  63.05  
2023-09-05 20:18:00 -0.006406 -0.026623  0.020217  63.07  
2023-09-05 20:25:00 -0.009917 -0.024108  0.014191  63.08  
2023-09-05 20:32:00 -0.010162 -0.019482  0.009320  63.11  

[2842 rows x 13 columns]

In [139]:
df2y

c
open_time                    
2023-08-23 01:05:00 -0.108091
2023-08-23 01:12:00  0.092750
2023-08-23 01:19:00  0.092664
2023-08-23 01:26:00 -0.216016
2023-08-23 01:33:00  0.015463
...                       ...
2023-09-05 20:04:00 -0.047574
2023-09-05 20:11:00  0.031731
2023-09-05 20:18:00  0.031721
2023-09-05 20:25:00  0.015855
2023-09-05 20:32:00  0.047559

[2842 rows x 1 columns]

In [170]:
df2x

h         l         v  num_trades  taker_base_vol  \
open_time                                                                       
2023-08-23 01:05:00  1.001544  0.999691  0.377598      0.1815        0.066152   
2023-08-23 01:12:00  1.002319  1.000000  0.207315      0.1355        0.054848   
2023-08-23 01:19:00  1.000309  0.998919  0.109815      0.0975        0.031956   
2023-08-23 01:26:00  1.000771  0.998611  0.219654      0.1125        0.088173   
2023-08-23 01:33:00  1.002319  0.999691  0.167335      0.0915        0.028230   
...                       ...       ...       ...         ...             ...   
2023-09-05 20:04:00  1.001269  0.999841  0.215119      0.1045        0.082101   
2023-09-05 20:11:00  1.000793  0.999683  0.105073      0.0825        0.018750   
2023-09-05 20:18:00  1.000634  0.999683  0.110810      0.1000        0.030114   
2023-09-05 20:25:00  1.001268  0.999841  0.083201      0.1050        0.019324   
2023-09-05 20:32:00  1.000476  0.999683  0.057320      0.0690        0.010873   

                         macd    macd_h    macd_s  
open_time                                          
2023-08-23 01:05:00  0.196127 -0.011405  0.207532  
2023-08-23 01:12:00  0.173237 -0.027436  0.200673  
2023-08-23 01:19:00  0.158116 -0.034046  0.192162  
2023-08-23 01:26:00  0.149253 -0.034327  0.183580  
2023-08-23 01:33:00  0.129440 -0.043312  0.172752  
...                       ...       ...       ...  
2023-09-05 20:04:00  0.022014 -0.018136  0.040150  
2023-09-05 20:11:00  0.008374 -0.025421  0.033795  
2023-09-05 20:18:00 -0.000813 -0.027686  0.026873  
2023-09-05 20:25:00 -0.006406 -0.026623  0.020217  
2023-09-05 20:32:00 -0.009917 -0.024108  0.014191  

[2842 rows x 8 columns]

In [120]:
####### test : 100% prediction
tp , tn ,fp,fn,allcorrect,allpred,sellsig,buysig=0,0,0,0,0,0,0,0
TestUSDTAmount=100
TestLTCAmount=0
for cc in range(1,len(df)-2):
    FLAGincprice  , FLAGincmoreprice, FLAGdecmoreprice, FLAGmarkovinc,FLAGincspeed,vote,risk=0,0,0,0,0,0,0
    y=df2y["c"][cc+1]
    price=df2y["c"][cc+1]
    # BUY Signal  and FLAGincmoreprice
    if(price>=0):
        buysig=buysig+1
        if(y>=0):
            tp=tp+1
        else:
            print(y)
            print(price)
            fp=fp+1
        
        TestLTCAmount=TestLTCAmount+float(TestUSDTAmount/float(np.array(df["price"][cc])))
        TestUSDTAmount=0
    
    else :
        sellsig=sellsig+1
        if(y<=0):
            tn=tn+1
        else:
            fn=fn+1
        TestUSDTAmount=TestUSDTAmount+float(TestLTCAmount*float(np.array(df["price"][cc])))
        TestLTCAmount=0

In [121]:
#print("ee"+ str(TestLTCAmount*float(myresult0[-1]))
#TestUSDTAmount
TestLTCAmount*float(np.array(df["price"][len(df)-1]))

418.26575849159667

In [122]:
print("tp:"+str(tp)+" tn:"+str(tn)+" fp:"+str(fp)+" fn:"+str(fn))

tp:1476 tn:1363 fp:0 fn:0


In [136]:
# test without covariates
train_transformed = TimeSeries.from_dataframe(df2ytr)
y_transformed = TimeSeries.from_dataframe(df2y)

covariates = datetime_attribute_timeseries(covariates, attribute="dayofweek", one_hot=False)
covariates = covariates.stack(
    datetime_attribute_timeseries(covariates, attribute="hour", one_hot=False)
)
covariates = covariates.stack(
    TimeSeries.from_times_and_values(
        times=covariates.time_index,
        values=np.arange(len(covariates)),
        columns=["linear_increase"],
    )
)
covariates = covariates.astype(np.float32)
covariates_transformed=covariates


tftmodel=TFTModel(input_chunk_length=19,output_chunk_length=1,hidden_size=70,lstm_layers=7,num_attention_heads=7,dropout=0.2,n_epochs=20, force_reset=True,
)

tftmodel.fit(train_transformed ,future_covariates=covariates_transformed, verbose=True)
tftmodel.save("full-ltc-tftmodel-without-covariates")



GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs

   | Name                              | Type                             | Params
----------------------------------------------------------------------------------------
0  | train_metrics                     | MetricCollection                 | 0     
1  | val_metrics                       | MetricCollection                 | 0     
2  | input_embeddings                  | _MultiEmbedding                  | 0     
3  | static_covariates_vsn             | _VariableSelectionNetwork        | 0     
4  | encoder_vsn                       | _VariableSelectionNetwork        | 7.6 K 
5  | decoder_vsn                       | _VariableSelectionNetwork        | 5.6 K 
6  | static_context_grn                | _GatedResidualNetwork            | 20.0 K
7  | static_context_hidden_encoder_grn | _GatedResidualNetwork            | 20.0 K
8  | static_cont

Training: |          | 0/? [00:00<?, ?it/s]

`Trainer.fit` stopped: `max_epochs=20` reached.


In [148]:
####### test 2w
tp , tn ,fp,fn,allcorrect,allpred,sellsig,buysig=0,0,0,0,0,0,0,0
TestUSDTAmount=100
TestLTCAmount=0
for cc in range(1,len(df)-21):
    FLAGincprice  , FLAGincmoreprice, FLAGdecmoreprice, FLAGmarkovinc,FLAGincspeed,vote,risk=0,0,0,0,0,0,0
    oldy=np.array(df2y["c"][cc:cc+19].tolist())
    y=np.array(df2y["c"][cc+19].tolist())
    
    oldy=pd.DataFrame(oldy,columns=['c'])
    oldy.index=pd.to_datetime(df2x[cc:cc+19].index,errors='ignore')
    #print (oldy)
    #print (df2x[cc:cc+19])
    #break
    #cov=pd.DataFrame(df2x[cc:cc+20])
    #cov.index=oldy.index
    test_transformed = TimeSeries.from_dataframe(oldy)
    #print (test_transformed)
    #break
    cov=TimeSeries.from_dataframe(pd.DataFrame(df2x[cc:cc+20]))
    #pastcov=TimeSeries.from_dataframe(pd.DataFrame(df2x[cc:cc+20]))
    #pastcov=TimeSeries.from_dataframe(cov)
    pastcov = datetime_attribute_timeseries(cov, attribute="dayofweek", one_hot=False )
    pastcov = pastcov.stack(datetime_attribute_timeseries(cov, attribute="hour", one_hot=False) )
    pastcov = pastcov.stack(
        TimeSeries.from_times_and_values(
            times=cov.time_index,
            values=np.arange(len(cov)),
            columns=["linear_increase"],
        )
    )
    price=model_test(test_transformed,pastcov)
    price=price[0]
    # BUY Signal  and FLAGincmoreprice
    if(price>=0):
        buysig=buysig+1
        if(y>=0):
            tp=tp+1
        else:
            fp=fp+1
        
        TestLTCAmount=TestLTCAmount+float(TestUSDTAmount/float(np.array(df["price"][cc+18])))
        TestUSDTAmount=0
    
    else :
        sellsig=sellsig+1
        if(y<=0):
            tn=tn+1
        else:
            fn=fn+1
        TestUSDTAmount=TestUSDTAmount+float(TestLTCAmount*float(np.array(df["price"][cc+18])))
        TestLTCAmount=0

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


...

Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

In [150]:
#print("ee"+ str(TestLTCAmount*float(myresult0[-1]))
#TestUSDTAmount
TestLTCAmount*float(np.array(df["price"][len(df)-1]))

100.8117702978508

In [151]:
print("tp:"+str(tp)+" tn:"+str(tn)+" fp:"+str(fp)+" fn:"+str(fn))

tp:747 tn:763 fp:663 fn:647


In [146]:
df2y

c
open_time                    
2023-08-23 01:05:00 -0.108091
2023-08-23 01:12:00  0.092750
2023-08-23 01:19:00  0.092664
2023-08-23 01:26:00 -0.216016
2023-08-23 01:33:00  0.015463
...                       ...
2023-09-05 20:04:00 -0.047574
2023-09-05 20:11:00  0.031731
2023-09-05 20:18:00  0.031721
2023-09-05 20:25:00  0.015855
2023-09-05 20:32:00  0.047559

[2842 rows x 1 columns]

In [147]:
df

o         h         l         c         v  \
open_time                                                            
2023-08-23 01:05:00  64.78  1.002319  1.000000 -0.108091  0.207315   
2023-08-23 01:12:00  64.69  1.000309  0.998919  0.092750  0.109815   
2023-08-23 01:19:00  64.75  1.000771  0.998611  0.092664  0.219654   
2023-08-23 01:26:00  64.81  1.002319  0.999691 -0.216016  0.167335   
2023-08-23 01:33:00  64.68  1.000618  0.999072  0.015463  0.219763   
...                    ...       ...       ...       ...       ...   
2023-09-05 20:04:00  63.06  1.000793  0.999683 -0.047574  0.105073   
2023-09-05 20:11:00  63.04  1.000634  0.999683  0.031731  0.110810   
2023-09-05 20:18:00  63.06  1.001268  0.999841  0.031721  0.083201   
2023-09-05 20:25:00  63.07  1.000476  0.999683  0.015855  0.057320   
2023-09-05 20:32:00  63.07  1.000317  0.999208  0.047559  0.045857   

                     num_trades          qav  taker_base_vol  taker_quote_vol  \
open_time                                                                       
2023-08-23 01:05:00      0.1355  80141.96408        0.054848      35529.57040   
2023-08-23 01:12:00      0.0975  42420.03428        0.031956      20686.10874   
2023-08-23 01:19:00      0.1125  84964.78687        0.088173      57156.09035   
2023-08-23 01:26:00      0.0915  64609.81340        0.028230      18265.05785   
2023-08-23 01:33:00      0.1005  84848.25773        0.110272      71342.20970   
...                         ...          ...             ...              ...   
2023-09-05 20:04:00      0.0825  39527.21648        0.018750      11819.74811   
2023-09-05 20:11:00      0.1000  41698.81910        0.030114      18987.71704   
2023-09-05 20:18:00      0.1050  31335.54841        0.019324      12196.32210   
2023-09-05 20:25:00      0.0690  21582.17306        0.010873       6859.50568   
2023-09-05 20:32:00      0.0420  17265.66719        0.005112       3224.77933   

                         macd    macd_h    macd_s  price  
open_time                                                 
2023-08-23 01:05:00  0.173237 -0.027436  0.200673  64.69  
2023-08-23 01:12:00  0.158116 -0.034046  0.192162  64.75  
2023-08-23 01:19:00  0.149253 -0.034327  0.183580  64.81  
2023-08-23 01:26:00  0.129440 -0.043312  0.172752  64.67  
2023-08-23 01:33:00  0.113240 -0.047610  0.160850  64.68  
...                       ...       ...       ...    ...  
2023-09-05 20:04:00  0.008374 -0.025421  0.033795  63.03  
2023-09-05 20:11:00 -0.000813 -0.027686  0.026873  63.05  
2023-09-05 20:18:00 -0.006406 -0.026623  0.020217  63.07  
2023-09-05 20:25:00 -0.009917 -0.024108  0.014191  63.08  
2023-09-05 20:32:00 -0.010162 -0.019482  0.009320  63.11  

[2842 rows x 13 columns]

In [168]:
#should delete:
tftmodel=TFTModel.load("full-ltc-tftmodel.pt")
####### test 2w
tp , tn ,fp,fn,allcorrect,allpred,sellsig,buysig=0,0,0,0,0,0,0,0
TestUSDTAmount=100
TestLTCAmount=0
for cc in range(1,len(df)-21):
    FLAGincprice  , FLAGincmoreprice, FLAGdecmoreprice, FLAGmarkovinc,FLAGincspeed,vote,risk=0,0,0,0,0,0,0
    oldy=np.array(df2y["c"][cc:cc+19].tolist())
    y=np.array(df2y["c"][cc+18].tolist())
    
    oldy=pd.DataFrame(oldy,columns=['c'])
    oldy.index=pd.to_datetime(df2x[cc:cc+19].index,errors='ignore')
    #print (oldy)
    #print (df2x[cc:cc+19])
    #break
    #cov=pd.DataFrame(df2x[cc:cc+20])
    #cov.index=oldy.index
    test_transformed = TimeSeries.from_dataframe(oldy)
    #print (test_transformed)
    #break
    pastcov=TimeSeries.from_dataframe(pd.DataFrame(df2x[cc:cc+20]))
    #pastcov=TimeSeries.from_dataframe(cov)
    pastcov = pastcov.stack(datetime_attribute_timeseries(pastcov, attribute="dayofweek", one_hot=False ))
    pastcov = pastcov.stack(datetime_attribute_timeseries(pastcov, attribute="hour", one_hot=False) )
    pastcov = pastcov.stack(
        TimeSeries.from_times_and_values(
            times=pastcov.time_index,
            values=np.arange(len(pastcov)),
            columns=["linear_increase"],
        )
    )
    price=model_test(test_transformed,pastcov)
    price=price[0]
    # BUY Signal  and FLAGincmoreprice
    if(price>=0):
        buysig=buysig+1
        if(y>=0):
            tp=tp+1
        else:
            fp=fp+1
        
        TestLTCAmount=TestLTCAmount+float(TestUSDTAmount/float(np.array(df["price"][cc+19])))
        TestUSDTAmount=0
    
    else :
        sellsig=sellsig+1
        if(y<=0):
            tn=tn+1
        else:
            fn=fn+1
        TestUSDTAmount=TestUSDTAmount+float(TestLTCAmount*float(np.array(df["price"][cc+19])))
        TestLTCAmount=0

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


...

Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

In [172]:
#print("ee"+ str(TestLTCAmount*float(myresult0[-1]))
print(TestUSDTAmount)
TestLTCAmount*float(np.array(df["price"][len(df)-1]))

0


98.61945365703917

In [171]:
####### test 2w
tp , tn ,fp,fn,allcorrect,allpred,sellsig,buysig=0,0,0,0,0,0,0,0
TestUSDTAmount=100
TestLTCAmount=0
for cc in range(1,len(df)-21):
    FLAGincprice  , FLAGincmoreprice, FLAGdecmoreprice, FLAGmarkovinc,FLAGincspeed,vote,risk=0,0,0,0,0,0,0
    oldy=np.array(df2y["c"][cc:cc+19].tolist())
    y=np.array(df2y["c"][cc+19].tolist())
    
    oldy=pd.DataFrame(oldy,columns=['c'])
    oldy.index=pd.to_datetime(df2x[cc:cc+19].index,errors='ignore')
    #print (oldy)
    #print (df2x[cc:cc+19])
    #break
    #cov=pd.DataFrame(df2x[cc:cc+20])
    #cov.index=oldy.index
    test_transformed = TimeSeries.from_dataframe(oldy)
    #print (test_transformed)
    #break
    pastcov=TimeSeries.from_dataframe(pd.DataFrame(df2x[cc:cc+20]))
    #pastcov=TimeSeries.from_dataframe(cov)
    pastcov = pastcov.stack(datetime_attribute_timeseries(pastcov, attribute="dayofweek", one_hot=False ))
    pastcov = pastcov.stack(datetime_attribute_timeseries(pastcov, attribute="hour", one_hot=False) )
    pastcov = pastcov.stack(
        TimeSeries.from_times_and_values(
            times=pastcov.time_index,
            values=np.arange(len(pastcov)),
            columns=["linear_increase"],
        )
    )
    price=model_test(test_transformed,pastcov)
    price=price[0]
    # BUY Signal  and FLAGincmoreprice
    if(price>=0):
        buysig=buysig+1
        if(y>=0):
            tp=tp+1
        else:
            fp=fp+1
        
        TestLTCAmount=TestLTCAmount+float(TestUSDTAmount/float(np.array(df["price"][cc+19])))
        TestUSDTAmount=0
    
    else :
        sellsig=sellsig+1
        if(y<=0):
            tn=tn+1
        else:
            fn=fn+1
        TestUSDTAmount=TestUSDTAmount+float(TestLTCAmount*float(np.array(df["price"][cc+19])))
        TestLTCAmount=0

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


...

Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]